In [33]:
import pandas as pd
import os
import numpy as np
import matplotlib.pyplot as plt
from math import *
from tqdm import tqdm
import cv2
import math

In [34]:
path = os.path.abspath(os.path.curdir)
path

'/Users/kaiweizhao/Desktop/ELEC5020/opencv/python 2'

In [35]:
result_path = os.path.join(path, 'result')
if not os.path.exists(result_path):
    result_path = os.mkdir(os.path.join(path, 'result'))
else:
    print(result_path, 'is exists!')

/Users/kaiweizhao/Desktop/ELEC5020/opencv/python 2/result is exists!


In [36]:
res = os.listdir(result_path)  # list 
num = len(res)
res

[]

In [37]:
img_name = str(num) + '.jpg'
img_name

'0.jpg'

In [38]:
file_path = os.path.join(path, 'data.xlsx')
print(file_path)
if not os.path.exists(file_path):
    raise Exception('error')
else:
    print('file exists! file path: ', file_path)
    df = pd.read_excel(file_path)

/Users/kaiweizhao/Desktop/ELEC5020/opencv/python 2/data.xlsx
file exists! file path:  /Users/kaiweizhao/Desktop/ELEC5020/opencv/python 2/data.xlsx


In [39]:
df.head()

Unnamed: 0  %Timestamp[s]  AP_index  pixel_GT_X  pixel_GT_Y  pixel_AP_X  \
0           0         1894.6         1          36         492         623   
1           1         1894.7         2          36         492         472   
2           2         1894.7         3          36         492         489   
3           3         1895.2         1          36         492         623   
4           4         1895.3         2          36         492         472   

   pixel_AP_Y  pt1_x  pt1_y  pt2_x  pt2_y  pt3_x  pt3_y  pt4_x  pt4_y  
0         501     35    539     37    445    622    548    624    454  
1         501     35    539     37    445    471    548    473    454  
2         297     35    539     37    445    488    548    490    454  
3         501     35    539     37    445    622    548    624    454  
4         501     35    539     37    445    471    548    473    454

In [40]:
data = df.loc[0]
pt1 = [int(data['pt1_x']), int(data['pt1_y'])]
pt2 = [int(data['pt2_x']), int(data['pt2_y'])]
pt3 = [int(data['pt3_x']), int(data['pt3_y'])]
pt4 = [int(data['pt4_x']), int(data['pt4_y'])]
print('pt1 = ', pt1)
print('pt2 = ', pt2)
print('pt3 = ', pt3)
print('pt4 = ', pt4)

pt1 =  [35, 539]
pt2 =  [37, 445]
pt3 =  [622, 548]
pt4 =  [624, 454]


In [41]:
img = cv2.imread(os.path.join(path, 'Floor-Plan.jpeg'))
newImagePath = os.path.join(result_path, img_name)

In [42]:
def rotate(
        img,
        pt1, pt2, pt3, pt4,
        newImagePath
):
    print('pt1 = ', pt1, 'pt2 = ', pt2, 'pt3 = ', pt3, 'pt4 = ', pt4)
    withRect = math.sqrt((pt4[0] - pt1[0]) ** 2 +
                         (pt4[1] - pt1[1]) ** 2)  # 矩形框的宽度
    heightRect = math.sqrt((pt1[0] - pt2[0]) ** 2 + (pt1[1] - pt2[1]) ** 2)
    print(withRect, heightRect)
    angle = acos((pt4[0] - pt1[0]) / withRect) * (180 / math.pi)  # 矩形框旋转角度\
    print(angle)

#     if pt4[1] > pt1[1]:
#         print("顺时针旋转")
#     else:
#         print("逆时针旋转")
#         angle = -angle

    height = img.shape[0]  # 原始图像高度
    width = img.shape[1]   # 原始图像宽度
    rotateMat = cv2.getRotationMatrix2D(
        (width / 2, height / 2), angle, 1)  # 按angle角度旋转图像
    heightNew = int(width * fabs(sin(radians(angle))) +
                    height * fabs(cos(radians(angle))))
    widthNew = int(height * fabs(sin(radians(angle))) +
                   width * fabs(cos(radians(angle))))

    rotateMat[0, 2] += (widthNew - width) / 2
    rotateMat[1, 2] += (heightNew - height) / 2
    imgRotation = cv2.warpAffine(
        img, rotateMat, (widthNew, heightNew))

    # 旋转后图像的四点坐标
    [[pt1[0]], [pt1[1]]] = np.dot(
        rotateMat, np.array([[pt1[0]], [pt1[1]], [1]]))
    [[pt3[0]], [pt3[1]]] = np.dot(
        rotateMat, np.array([[pt3[0]], [pt3[1]], [1]]))
    [[pt2[0]], [pt2[1]]] = np.dot(
        rotateMat, np.array([[pt2[0]], [pt2[1]], [1]]))
    [[pt4[0]], [pt4[1]]] = np.dot(
        rotateMat, np.array([[pt4[0]], [pt4[1]], [1]]))

    # 处理反转的情况
    if pt2[1] > pt4[1]:
        pt2[1], pt4[1] = pt4[1], pt2[1]
    if pt1[0] > pt3[0]:
        pt1[0], pt3[0] = pt3[0], pt1[0]

    imgOut = imgRotation[int(pt2[1]):int(pt4[1]), int(pt1[0]):int(pt3[0])]

    # print(imgOut)

    cv2.imwrite(newImagePath, imgOut) 

## 新写的 rotate

In [43]:
def rotate(
        img,
        pt1, pt2, pt3, pt4,
        newImagePath
):
    """ 旋转 """
#     print('pt1 = ', pt1, 'pt2 = ', pt2, 'pt3 = ', pt3, 'pt4 = ', pt4)
    withRect = math.sqrt((pt4[0] - pt1[0]) ** 2 +
                         (pt4[1] - pt1[1]) ** 2)  # 矩形框的宽度，这个是变长的边
    heightRect = math.sqrt((pt1[0] - pt2[0]) ** 2 + (pt1[1] - pt2[1]) ** 2)  # 这个是指定的像素点对应的边
#     print(withRect, heightRect)
    angle = acos((pt4[0] - pt1[0]) / withRect) * (180 / math.pi)  # 矩形框旋转角度\
    print(angle)

    if pt4[1] > pt1[1]:
        print("顺时针旋转")
    else:
        print("逆时针旋转")
        angle = -angle

    height = img.shape[0]  # 原始图像高度
    width = img.shape[1]   # 原始图像宽度
    rotateMat = cv2.getRotationMatrix2D(
        (width / 2, height / 2), angle, 1)  # 按angle角度旋转图像
    heightNew = int(width * fabs(sin(radians(angle))) +
                    height * fabs(cos(radians(angle))))
    widthNew = int(height * fabs(sin(radians(angle))) +
                   width * fabs(cos(radians(angle))))

    rotateMat[0, 2] += (widthNew - width) / 2
    rotateMat[1, 2] += (heightNew - height) / 2
    imgRotation = cv2.warpAffine(
        img, rotateMat, (widthNew, heightNew))

    # 旋转后图像的四点坐标
    [[pt1[0]], [pt1[1]]] = np.dot(
        rotateMat, np.array([[pt1[0]], [pt1[1]], [1]]))
    [[pt3[0]], [pt3[1]]] = np.dot(
        rotateMat, np.array([[pt3[0]], [pt3[1]], [1]]))
    [[pt2[0]], [pt2[1]]] = np.dot(
        rotateMat, np.array([[pt2[0]], [pt2[1]], [1]]))
    [[pt4[0]], [pt4[1]]] = np.dot(
        rotateMat, np.array([[pt4[0]], [pt4[1]], [1]]))

    # 处理反转的情况
    if pt2[1] > pt4[1]:
        pt2[1], pt4[1] = pt4[1], pt2[1]
    if pt1[0] > pt3[0]:
        pt1[0], pt3[0] = pt3[0], pt1[0]

    imgOut = imgRotation[int(pt2[1]):int(pt4[1]), int(pt1[0]):int(pt3[0])]

    # print(imgOut)

    cv2.imwrite(newImagePath, imgOut) 

In [44]:
count = 0
for i in range(len(df)):
    # # 1.确定参数
    # 参数1:新保存的文件路径 newImagePath
    res = os.listdir(result_path)  # list 
    num = len(res)
    img_name = str(num) + '.jpg'
    newImagePath = os.path.join(result_path, img_name)
    # 参数2:image
    # 参数3:四个坐标点
    data = df.loc[i]
    
    pt1 = [int(data['pt1_x']), int(data['pt1_y'])]
    pt2 = [int(data['pt2_x']), int(data['pt2_y'])]
    pt3 = [int(data['pt3_x']), int(data['pt3_y'])]
    pt4 = [int(data['pt4_x']), int(data['pt4_y'])]
    
    tmp=[pt1,pt2,pt3,pt4]
    pt_3 = max(pt1,pt2,pt3,pt4, key=lambda x: x[0])
    pt_1 = min(pt1, pt2, pt3, pt4, key=lambda x: x[0])  # 
    pt_2 = min(pt1,pt2,pt3,pt4,key=lambda x:x[1])
    pt_4= max(pt1,pt2,pt3,pt4,key=lambda x:x[1])

#     print('pt_1=',pt_1,'pt_2=',pt_2,'pt_3=',pt_3,'pt_4=',pt_4)
    
    # 获取矩形的长和宽
    withRect = math.sqrt((pt_4[0] - pt_1[0]) ** 2 +
                         (pt_4[1] - pt_1[1]) ** 2)  # 矩形框的宽度，这个是变长的边
    heightRect = math.sqrt((pt_1[0] - pt_2[0]) ** 2 + 
                           (pt_1[1] - pt_2[1]) ** 2)  # 这个是指定的像素点对应的边
#     print('withRect: ', withRect)
#     print('heightRect: ', heightRect)

    # # # 过滤异常点
    # # # 378是根据指定宽度计算出来的
    if abs(withRect - 95) > 3 and abs(heightRect - 95) > 3:
        print('error!')
        print('withRect: ', withRect)
        print('heightRect: ', heightRect)
        print('=' * 20)
        count += 1
        continue
    # 只需要判断一步 pt_1和 pt_2 之间的距离是不是 指定宽度 即可
    if abs(heightRect - 95) > 3:
        pt_1, pt_2, pt_3, pt_4 = pt_4, pt_1, pt_2, pt_3
    
    withRect = math.sqrt((pt_4[0] - pt_1[0]) ** 2 +
                         (pt_4[1] - pt_1[1]) ** 2)  # 矩形框的宽度，这个是变长的边
    heightRect = math.sqrt((pt_1[0] - pt_2[0]) ** 2 + 
                           (pt_1[1] - pt_2[1]) ** 2)  # 这个是指定的像素点对应的边
    print('修整过后的 heightRect = ', heightRect, 'withRect = ', withRect)
    if abs(withRect - 94) > 3 and abs(heightRect - 94) > 3:
        raise Exception('异常大小 error!')
    
#     pt2 = [234, 540]
#     pt1 = [234, 508]
#     pt4 = [342, 508]
#     pt3 = [342, 540]
    # # 2.rotate操作
    try:
        rotate(img, pt_1, pt_2, pt_3, pt_4, newImagePath)
    except:
        print('异常点的 heightRect = ', heightRect, 'withRect = ', withRect)
        continue

print('异常点个数：count = ', count)

修整过后的 heightRect =  94.02127418834527 withRect =  587.0689908349784
0.8784013878691193
顺时针旋转
修整过后的 heightRect =  94.02127418834527 withRect =  436.09288001525545
1.1825431033407117
顺时针旋转
修整过后的 heightRect =  94.02127418834527 withRect =  453.0893951528771
1.138177007488375
顺时针旋转
修整过后的 heightRect =  94.02127418834527 withRect =  587.0689908349784
0.8784013878691193
顺时针旋转
修整过后的 heightRect =  94.02127418834527 withRect =  436.09288001525545
1.1825431033407117
顺时针旋转
修整过后的 heightRect =  94.02127418834527 withRect =  453.0893951528771
1.138177007488375
顺时针旋转
修整过后的 heightRect =  94.02127418834527 withRect =  587.0689908349784
0.8784013878691193
顺时针旋转
修整过后的 heightRect =  94.02127418834527 withRect =  436.09288001525545
1.1825431033407117
顺时针旋转
修整过后的 heightRect =  94.02127418834527 withRect =  453.0893951528771
1.138177007488375
顺时针旋转
修整过后的 heightRect =  94.02127418834527 withRect =  587.0689908349784
0.8784013878691193
顺时针旋转
修整过后的 heightRect =  94.02127418834527 withRect =  436.09288001525545
1

In [45]:
img = cv2.imread('/Users/kaiweizhao/Desktop/python 2/python/office.jpeg')
newImagePath = os.path.join(result_path, img_name)
pt1 = [33, 681]
pt2 = [39, 303]
pt4 = [620, 690]
pt3 = [626, 312]
rotate(img,
        pt1, pt2, pt3, pt4,
        newImagePath)

0.8784013878691193
顺时针旋转


AttributeError: 'NoneType' object has no attribute 'shape'